<a href="https://colab.research.google.com/github/Naeima/fooKG/blob/main/foo_KG.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Query FOO from URI (COLAB)


In [2]:
## Install Libraries
# !pip install rdflib
# !pip install requests
# !pip install SPARQLWrapper
# !pip install rdflib spacy
# !pip python -m spacy download en_core_web_sm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 565.1/565.1 kB 21.6 MB/s eta 0:00:00
ERROR: unknown command "python"


In [17]:
# Import installed libraries
import io
import os
import rdflib
from rdflib import URIRef, Literal, Graph, RDF, Namespace, plugin
from rdflib.plugins import sparql
from rdflib.plugins.sparql import prepareQuery
from rdflib.parser import Parser
from rdflib import Graph
from rdflib.plugins.sparql import prepareQuery
from SPARQLWrapper import SPARQLWrapper, JSON, N3
import requests
import json
from SPARQLWrapper import SPARQLWrapper, JSON
import spacy
from rdflib import Graph
import folium
from folium.plugins import MarkerCluster
from geopy.distance import geodesic

In [18]:
# RDF Data Extraction
foo_KG = Graph()
foo_KG.parse("https://naeima.github.io/fooKG/index.ttl", format="ttl")

query = """
PREFIX foo: <https://w3id.org/def/foo#>

SELECT ?id ?latitude ?longitude ?localDate
WHERE {
  ?s a foo:gPSObservation ;
     foo:id ?id ;
     foo:latitude ?latitude ;
     foo:longitude ?longitude ;
     foo:localDate ?localDate .
}
ORDER BY ?localDate
LIMIT 100
"""

data = {'ID': [], 'Latitude': [], 'Longitude': [], 'Timestamp': []}

for row in foo_KG.query(query):
    try:
        data['ID'].append(str(row.id))
        data['Latitude'].append(float(row.latitude))
        data['Longitude'].append(float(row.longitude))
        data['Timestamp'].append(str(row.localDate))
    except:
        continue

# --- Map Setup ---
m = folium.Map(location=[data['Latitude'][0], data['Longitude'][0]], zoom_start=13, tiles=None)

folium.TileLayer(
    tiles='https://{s}.googleapis.com/vt/lyrs=s&x={x}&y={y}&z={z}',
    attr='Google',
    name='Google Satellite',
    max_zoom=20,
    subdomains=['mt0', 'mt1', 'mt2', 'mt3'],
    overlay=False,
    control=True,
).add_to(m)

marker_cluster = MarkerCluster().add_to(m)

# --- Add Markers ---
for i in range(len(data['ID'])):
    folium.Marker(
        location=[data['Latitude'][i], data['Longitude'][i]],
        popup=f"<i>ID: {data['ID'][i]}</i>",
        tooltip=data['Timestamp'][i],
    ).add_to(marker_cluster)

# --- Draw Lines + Show Distances ---
for i in range(1, len(data['ID'])):
    point1 = (data['Latitude'][i - 1], data['Longitude'][i - 1])
    point2 = (data['Latitude'][i], data['Longitude'][i])
    distance_km = geodesic(point1, point2).kilometers

    # Draw line
    folium.PolyLine(
        locations=[point1, point2],
        color='red',
        weight=2,
        tooltip=f"{distance_km:.2f} km"
    ).add_to(m)

# --- Display the map ---
m
